#Apartment Hunting in Reverse 

###What problems of a neighborhood can 311 complaints reveal? 

###Spe Chen @spepechen

file source: https://nycopendata.socrata.com/Social-Services/311-Service-Requests-from-2010-to-Present/erm2-nwe9
2015/08/24 15:17 (Watch out! It takes a ~long~ while to download.) 😴

<a href="http://imgur.com/d1fZmvb"><img src="http://i.imgur.com/d1fZmvb.png?1" title="source: imgur.com" /></a>

Overview of Data Processing

<a href="http://imgur.com/i3e3Vx3"><img src="http://i.imgur.com/i3e3Vx3.png" title="source: imgur.com" /></a>

Here's the map. 
https://spe.cartodb.com/viz/877ec864-4ec9-11e5-aace-0e018d66dc29/public_map

#Step 1: Extracting Subset

##Using Command Line to Get Information about the Data Set 

http://bconnelly.net/working-with-csvs-on-the-command-line/#getting-information-about-the-data-set

In [4]:
!head -n1 311whole.csv

Unique Key,Created Date,Closed Date,Agency,Agency Name,Complaint Type,Descriptor,Location Type,Incident Zip,Incident Address,Street Name,Cross Street 1,Cross Street 2,Intersection Street 1,Intersection Street 2,Address Type,City,Landmark,Facility Type,Status,Due Date,Resolution Description,Resolution Action Updated Date,Community Board,Borough,X Coordinate (State Plane),Y Coordinate (State Plane),Park Facility Name,Park Borough,School Name,School Number,School Region,School Code,School Phone Number,School Address,School City,School State,School Zip,School Not Found,School or Citywide Complaint,Vehicle Type,Taxi Company Borough,Taxi Pick Up Location,Bridge Highway Name,Bridge Highway Direction,Road Ramp,Bridge Highway Segment,Garage Lot Name,Ferry Direction,Ferry Terminal Name,Latitude,Longitude,Location


In [2]:
header ="Uniqlue Key,Created Date,Closed Date,Agency,Agency Name,Complaint Type,Descriptor,Location Type,Incident Zip,Incident Address,Street Name,Cross Street 1,Cross Street 2,Intersection Street 1,Intersection Street 2,Address Type,City,Landmark,Facility Type,Status,Due Date,Resolution Description,Resolution Action Updated Date,Community Board,Borough,X Coordinate (State Plane),Y Coordinate (State Plane),Park Facility Name,Park Borough,School Name,School Number,School Region,School Code,School Phone Number,School Address,School City,School State,School Zip,School Not Found,School or Citywide Complaint,Vehicle Type,Taxi Company Borough,Taxi Pick Up Location,Bridge Highway Name,Bridge Highway Direction,Road Ramp,Bridge Highway Segment,Garage Lot Name,Ferry Direction,Ferry Terminal Name,Latitude,Longitude,Location"
header.count(',') #(the number of comma + 1) = num of columns #53 columns 

52

http://stackoverflow.com/questions/1155617/count-occurrence-of-a-character-in-a-string

In [3]:
!wc -l 311whole.csv #9786496 rows including a header #almost 10 million rows 

 9786496 311whole.csv


###<font color = blue> The size is 9786496 rows X 53 columns. (6.13 GB) 😲😱😲😱😲😱😲😱😲😱

##So it's time for data massage!

http://stackoverflow.com/questions/577892/what-does-data-massage-mean

##Checking whether there are comments in rows. 

In [6]:
!grep "#" 311whole.csv | wc -l #2130 rows contain comments. 

    2130


In [8]:
!grep "#" 311whole.csv | head -n 1 #It seems to be a sign for number, but not metadata. So keep it at the stage. 

31305134,08/13/2015 05:30:52 PM,08/20/2015 12:38:22 PM,DOT,Department of Transportation,Broken Muni Meter,No Receipt,Lot,11214,,,86 STREET,18 AVENUE,,,,BROOKLYN,,N/A,Closed,09/03/2015 05:30:52 PM,"The Department of Transportation inspected the condition you reported. You can find additional information in the ""Notes to Customer"" field.",08/20/2015 12:38:22 PM,11 BROOKLYN,BROOKLYN,983516,160517,Unspecified,BROOKLYN,Unspecified,Unspecified,Unspecified,Unspecified,Unspecified,Unspecified,Unspecified,Unspecified,Unspecified,N,,,,,,,,,Bensonhurst #1 Field,,,40.60725840274471,-74.00264345847668,"(40.60725840274471, -74.00264345847668)"


##Adding index to header so I will know which columns to extract from the whole file 🙌 

In [29]:
header ="Unique Key,Created Date,Closed Date,Agency,Agency Name,Complaint Type,Descriptor,Location Type,Incident Zip,Incident Address,Street Name,Cross Street 1,Cross Street 2,Intersection Street 1,Intersection Street 2,Address Type,City,Landmark,Facility Type,Status,Due Date,Resolution Description,Resolution Action Updated Date,Community Board,Borough,X Coordinate (State Plane),Y Coordinate (State Plane),Park Facility Name,Park Borough,School Name,School Number,School Region,School Code,School Phone Number,School Address,School City,School State,School Zip,School Not Found,School or Citywide Complaint,Vehicle Type,Taxi Company Borough,Taxi Pick Up Location,Bridge Highway Name,Bridge Highway Direction,Road Ramp,Bridge Highway Segment,Garage Lot Name,Ferry Direction,Ferry Terminal Name,Latitude,Longitude,Location"
header_list = header.split(',')
for index, value in enumerate(header_list): 
    print index, value


0 Unique Key
1 Created Date
2 Closed Date
3 Agency
4 Agency Name
5 Complaint Type
6 Descriptor
7 Location Type
8 Incident Zip
9 Incident Address
10 Street Name
11 Cross Street 1
12 Cross Street 2
13 Intersection Street 1
14 Intersection Street 2
15 Address Type
16 City
17 Landmark
18 Facility Type
19 Status
20 Due Date
21 Resolution Description
22 Resolution Action Updated Date
23 Community Board
24 Borough
25 X Coordinate (State Plane)
26 Y Coordinate (State Plane)
27 Park Facility Name
28 Park Borough
29 School Name
30 School Number
31 School Region
32 School Code
33 School Phone Number
34 School Address
35 School City
36 School State
37 School Zip
38 School Not Found
39 School or Citywide Complaint
40 Vehicle Type
41 Taxi Company Borough
42 Taxi Pick Up Location
43 Bridge Highway Name
44 Bridge Highway Direction
45 Road Ramp
46 Bridge Highway Segment
47 Garage Lot Name
48 Ferry Direction
49 Ferry Terminal Name
50 Latitude
51 Longitude
52 Location


http://stackoverflow.com/questions/522563/accessing-the-index-in-python-for-loops

I need these 8 columns:
```
1 Created Date
4 Agency Name
5 Complaint Type
6 Descriptor
8 Incident Zip
24 Borough
50 Latitude
51 Longitude
```

In [30]:
#Get first 1000 rows of the file as sample 

!head -n 1000 311whole.csv > first1000.csv

In [44]:
import csv
reader = csv.reader(open("first1000.csv", 'rU'))

for column in reader:
    if column[50] and column[51]: #check the value of latitude and longtitud are not empty
        #extract the columns I need and turn it into CSV-like row 
        print ", ".join([column[1], column[4], column[5], column[6], column[8], column[24], column[50], column[51],]) + "\n"

Created Date, Agency Name, Complaint Type, Descriptor, Incident Zip, Borough, Latitude, Longitude

08/23/2015 02:15:14 AM, New York City Police Department, Noise - Street/Sidewalk, Loud Music/Party, 10040, MANHATTAN, 40.8618290295582, -73.9294560541168

08/23/2015 02:15:00 AM, New York City Police Department, Illegal Parking, Double Parked Blocking Traffic, 10031, MANHATTAN, 40.82612184147712, -73.94765068494952

08/23/2015 02:14:43 AM, New York City Police Department, Noise - Commercial, Loud Music/Party, 11237, BROOKLYN, 40.70657442499495, -73.92286480063883

08/23/2015 02:14:00 AM, New York City Police Department, Noise - Vehicle, Car/Truck Music, 11413, QUEENS, 40.67286072356791, -73.74830684675992

08/23/2015 02:13:48 AM, New York City Police Department, Noise - Street/Sidewalk, Loud Music/Party, 10468, BRONX, 40.8610726526304, -73.90112824093595

08/23/2015 02:13:43 AM, New York City Police Department, Noise - Street/Sidewalk, Loud Talking, 11238, BROOKLYN, 40.68351286257578, -73

http://stackoverflow.com/questions/9573244/most-elegant-way-to-check-if-the-string-is-empty-in-python

In [10]:
import csv
reader = csv.reader(open("first1000.csv", 'rU'))
filtered = open("first1000_filtered_delimiter.csv", "w")

for column in reader:
    if column[50] and column[51]: #check the value of latitude and longtitud are not empty        
        filtered.write(",".join([column[1], column[4], column[5], column[6], column[8], column[24], column[50], column[51],]) + "\n", delimiter ='|')

TypeError: write() takes no keyword arguments

In [50]:
# This takes about 2 min to generate the file....
import csv
reader = csv.reader(open("311whole.csv", 'rU'))
filtered = open("whole_filtered.csv", "w")

for column in reader:
    if column[50] and column[51]: #check the value of latitude and longtitud are not empty        
        filtered.write(",".join([column[1], column[4], column[5], column[6], column[8], column[24], column[50], column[51],]) + "\n")

http://stackoverflow.com/questions/886237/how-can-i-randomize-the-lines-in-a-file-using-standard-tools-on-red-hat-linux

In [51]:
!head -n10 whole_filtered.csv

Created Date,Agency Name,Complaint Type,Descriptor,Incident Zip,Borough,Latitude,Longitude
08/23/2015 02:15:14 AM,New York City Police Department,Noise - Street/Sidewalk,Loud Music/Party,10040,MANHATTAN,40.8618290295582,-73.9294560541168
08/23/2015 02:15:00 AM,New York City Police Department,Illegal Parking,Double Parked Blocking Traffic,10031,MANHATTAN,40.82612184147712,-73.94765068494952
08/23/2015 02:14:43 AM,New York City Police Department,Noise - Commercial,Loud Music/Party,11237,BROOKLYN,40.70657442499495,-73.92286480063883
08/23/2015 02:14:00 AM,New York City Police Department,Noise - Vehicle,Car/Truck Music,11413,QUEENS,40.67286072356791,-73.74830684675992
08/23/2015 02:13:48 AM,New York City Police Department,Noise - Street/Sidewalk,Loud Music/Party,10468,BRONX,40.8610726526304,-73.90112824093595
08/23/2015 02:13:43 AM,New York City Police Department,Noise - Street/Sidewalk,Loud Talking,11238,BROOKLYN,40.68351286257578,-73.96087245782502
08/23/2015 02:11:34 AM,New York City Po

In [52]:
!wc -l whole_filtered.csv #there are 8944124 rows X 8 columns containing info I want. #1.31 GB 

 8944124 whole_filtered.csv


Here is the problem, some values in cells contain delimiter ",".

So pandas will get confused when it read through lines, like this one:  

In [17]:
!sed -n "248 p" whole_filtered.csv

08/23/2015 12:07:21 AM,Department of Transportation,Street Sign - Missing,No Parking, Standing, Stopping,10027,MANHATTAN,40.81280954947035,-73.96039906177317


08/23/2015 12:07:21 AM,Department of Transportation,<font color = blue>Street Sign - Missing,No Parking, Standing, Stopping,</font>10027,MANHATTAN,40.81280954947035,-73.96039906177317

In [18]:
!head -n1 whole_filtered.csv

Created Date,Agency Name,Complaint Type,Descriptor,Incident Zip,Borough,Latitude,Longitude


##Keep massaging....😩

Just skipped those messy rows.

In [ ]:
import pandas as pd

df = pd.read_csv("whole_filtered.csv", error_bad_lines=False)

Skipping line 248: expected 8 fields, saw 10
Skipping line 257: expected 8 fields, saw 10
Skipping line 562: expected 8 fields, saw 9
Skipping line 581: expected 8 fields, saw 9
Skipping line 599: expected 8 fields, saw 9
Skipping line 667: expected 8 fields, saw 9
Skipping line 738: expected 8 fields, saw 9
Skipping line 760: expected 8 fields, saw 9
Skipping line 912: expected 8 fields, saw 9
Skipping line 1039: expected 8 fields, saw 9
Skipping line 1049: expected 8 fields, saw 9
Skipping line 1071: expected 8 fields, saw 9
Skipping line 1098: expected 8 fields, saw 9
Skipping line 1102: expected 8 fields, saw 9
Skipping line 1124: expected 8 fields, saw 9
Skipping line 1167: expected 8 fields, saw 9
Skipping line 1185: expected 8 fields, saw 9
Skipping line 1228: expected 8 fields, saw 9
Skipping line 1242: expected 8 fields, saw 9
Skipping line 1259: expected 8 fields, saw 9
Skipping line 1316: expected 8 fields, saw 9
Skipping line 1351: expected 8 fields, saw 9
Skipping line 136

In [15]:
df.shape #wiped out 185834 rows. 

(8758290, 8)

In [16]:
df.to_csv("whole_cleaned.csv")

http://stackoverflow.com/questions/18039057/python-pandas-error-tokenizing-data

In [1]:
!ipython nbconvert 311_extracting_slide.ipynb --to slides

[NbConvertApp] Converting notebook 311_extracting_slide.ipynb to slides
[NbConvertApp] Writing 7368752 bytes to 311_extracting_slide.slides.html


In [2]:
!ipython nbconvert 311_extracting_slide.ipynb --to slides --post serve

[NbConvertApp] Converting notebook 311_extracting_slide.ipynb to slides
[NbConvertApp] Writing 7368752 bytes to 311_extracting_slide.slides.html
[NbConvertApp] Redirecting reveal.js requests to https://cdn.jsdelivr.net/reveal.js/2.6.2
Traceback (most recent call last):
  File "/Users/Spepe/anaconda/bin/ipython", line 6, in <module>
    sys.exit(start_ipython())
  File "/Users/Spepe/anaconda/lib/python2.7/site-packages/IPython/__init__.py", line 120, in start_ipython
    return launch_new_instance(argv=argv, **kwargs)
  File "/Users/Spepe/anaconda/lib/python2.7/site-packages/IPython/config/application.py", line 574, in launch_instance
    app.start()
  File "/Users/Spepe/anaconda/lib/python2.7/site-packages/IPython/terminal/ipapp.py", line 367, in start
    return self.subapp.start()
  File "/Users/Spepe/anaconda/lib/python2.7/site-packages/IPython/nbconvert/nbconvertapp.py", line 278, in start
    self.convert_notebooks()
  File "/Users/Spepe/anaconda/lib/python2.7/site-packages/IPytho